# Taylor变换骨架 (Taylor-transformed skeletons)


## 1. 关于骨架的Taylor视频 (Taylor videos on skeletons)


In [8]:
import scipy
from scipy import io
import torch
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
from IPython.display import HTML, display
# 导入必要的库：
# scipy 用于加载mat文件，torch用于张量计算


In [4]:
def taylor_video(videoinput, terms, temporal_block):
    """
    对输入的视频骨架序列进行Taylor级数变换 (Apply Taylor series transformation to the skeleton video sequence).

    参数 (Parameters):
      videoinput: 存储骨架序列的mat文件路径 (the path of the mat file containing skeleton sequence)
      terms: Taylor级数展开项数 (number of Taylor series terms)
      temporal_block: 时间块的长度 (length of the temporal block)
    """

    def factorial(n):
        """
        使用递归计算输入张量中每个元素的阶乘 (calculate factorial of each element in the input tensor using recursion).
        """
        # 基本情况：0的阶乘为1 (base case: factorial of 0 is 1)
        if n == 0:
            return torch.tensor(1)
        else:
            return n * factorial(n - 1)

    # 假设步长为1 (assume stride = 1)
    video = torch.from_numpy(scipy.io.loadmat(videoinput)['skeletonsequence'])  # 20,3,54

    # 获取骨架、通道、时间帧的数量 (Joints, Channels, Time)
    J, C, T = video.shape  # 20,3,54

    if temporal_block - 1 < terms:
        print(
            '给定的时间块长度不足以计算定义的级数项 (The given temporal block length is not enough to compute terms defined).')
    else:
        # 初始化Taylor变换后的视频张量
        Taylor = torch.zeros((J, C, T - temporal_block + 1))

        # 对每个时间块进行操作 (process each temporal block)
        for i in range(T - temporal_block + 1):
            # 获取当前时间块内的骨架数据 (extract video clip for current block)
            video_clip = video[:, :, i:i + temporal_block]
            # 取时间块第一帧数据，并在第三个维度扩展 (get the first frame and repeat to match temporal block size)
            slice_tensor = video[:, :, i].unsqueeze(2)  # 20,3,1
            dummy_clip = slice_tensor.repeat(1, 1, temporal_block)  # 20,3,4

            # 计算时间差分 (compute temporal differences)
            delta_temp = video_clip - dummy_clip

            # 初始化一个存储各阶差分的张量 (store differences for each order)
            D_temp = torch.zeros(J, C, terms)

            # 复制当前视频片段用于计算高阶差分 (temp用于递归计算差分)
            temp = video_clip

            # 计算Taylor展开中各项的差分 (compute differences for each Taylor term)
            for j in range(terms):
                diff = temp[:, :, 1:] - temp[:, :, :-1]
                # 这里仅取第一帧的差分作为代表 (use the first difference of the current order)
                D_temp[:, :, j] = diff[:, :, 0]
                temp = diff

            # 初始化矩阵M，用于存放Taylor级数展开结果 (accumulate Taylor series expansion)
            M = torch.zeros((J, C, temporal_block))

            # 累加Taylor展开各阶项 (accumulate each order term)
            for order in range(terms):
                # 使用阶乘和差分，结合delta_temp的幂次 (combine factorial, difference and powers of delta)
                M = M + (D_temp[:, :, order].unsqueeze(-1) / factorial(order)) * torch.pow(delta_temp, order)

                # 计算当前时间块的平均值作为Taylor变换后的帧 (compute average over temporal block)
            taylor_frame = M.mean(2)

            Taylor[:, :, i] = taylor_frame

    return Taylor


In [5]:
# 指定输入的骨架数据文件 (specify input skeleton file)
sk = 'a01_s01_e01_skeleton3D.txtssq.mat'

# 加载原始骨架数据 (load original skeleton sequence)
skeleton = scipy.io.loadmat(sk)['skeletonsequence']

# 将numpy数组转换为torch张量 (convert numpy array to torch tensor)
skeleton = torch.from_numpy(skeleton)
print(skeleton.shape)

torch.Size([20, 3, 54])


## 2. 可视化原始骨架 (Visualisation of original skeletons)

In [23]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.animation import FuncAnimation
from IPython.display import HTML, display

# 获取视频帧数和关节数 (get number of frames and joints)
num_frames = skeleton.shape[2]  # 51
num_joints = skeleton.shape[0]  # 20

# 定义骨骼的连接关系 (connections of bones)
# 例如: 第1组连接 [12, 10, 8, 1, 2, 0, 7, 9, 11]
sk_config = [[12, 10, 8, 1, 2, 0, 7, 9, 11], [19, 2, 3, 6, 5, 14, 16, 18], [6, 4, 13, 15, 17]]


# 定义绘制二维骨架帧的函数 (function to plot 2D skeleton frame)
# 水平方向为x轴 (x as horizontal), 垂直方向为y轴 (y as vertical)
def plot_skeleton_frame_2d(frame_data, sk_config, ax):
    ax.clear()
    ax.set_title("2D Skeleton Frame (Horizontal X, Vertical Y)")

    # 绘制每个关节 (plot joints)
    for i in range(num_joints):
        x = frame_data[i, 0]
        y = frame_data[i, 1]
        ax.scatter(x, y, color='r')

        # 根据连接关系绘制骨骼 (plot bones based on connections)
    for connections in sk_config:
        for i in range(len(connections) - 1):
            start_joint = connections[i]
            end_joint = connections[i + 1]
            ax.plot([frame_data[start_joint, 0], frame_data[end_joint, 0]],
                    [frame_data[start_joint, 1], frame_data[end_joint, 1]], color='b')

            # 设置相等的比例 (set equal aspect ratio)
    ax.set_aspect('equal')


# 创建图像和坐标轴 (create figure and axis)
fig, ax = plt.subplots(figsize=(8, 8))

# 初始化显示第一帧 (initialize plot with the first frame)
plot_skeleton_frame_2d(skeleton[:, :, 0], sk_config, ax)


# 定义动画更新函数 (update function for animation)
def update(frame):
    plot_skeleton_frame_2d(skeleton[:, :, frame], sk_config, ax)


# 创建动画，间隔100毫秒 (create animation with 100ms interval)
ani = FuncAnimation(fig, update, frames=num_frames, interval=100)  # Interval in milliseconds

# 禁用坐标轴刻度和标签 (disable xticks, yticks, xlabel, and ylabel)
ax.set_xticks([])
ax.set_yticks([])
ax.set_xlabel('')
ax.set_ylabel('')

# 使用HTML显示动画 (display the animation using HTML)
html_anim = HTML(ani.to_jshtml())
display(html_anim)

# 关闭图像以避免重复显示 (close the plot)
plt.close()


## 3. 在原始骨架上可视化Taylor变换结果 (Visualisation of Taylor-transformed skeletons on original skeletons)

In [6]:
# 使用子序列长度为4，Taylor级数项数为3，仅考虑位移 (subsequence length = 4, terms = 3, displacement only)
taylorskeleton = taylor_video(sk, 3, 4)

# 输出Taylor变换后骨架数据的形状 (display shape of Taylor-transformed skeleton)
taylorskeleton.shape


torch.Size([20, 3, 51])

In [12]:
num_taylor = taylorskeleton.shape[2]  # 51
num_frames = skeleton.shape[2]  # 54
num_joints = skeleton.shape[0]  # 20

# 定义骨骼连接关系 (connections of bones)
sk_config = [[12, 10, 8, 1, 2, 0, 7, 9, 11], [19, 2, 3, 6, 5, 14, 16, 18], [6, 4, 13, 15, 17]]


# 定义绘制二维骨架帧的函数，同时显示Taylor变换结果 (plot 2D skeleton frame with Taylor transformation)
def plot_skeleton_frame_2d(frame_data, taylor_data, sk_config, ax):
    ax.clear()
    ax.set_title("2D Skeleton Frame (Horizontal X, Vertical Y)")

    # 绘制每个关节，并根据Taylor变换数据调整点的大小 (plot joints and adjust point size based on Taylor data)
    for i in range(num_joints):
        x = frame_data[i, 0]
        y = frame_data[i, 1]
        a = taylor_data[i, 0]
        b = taylor_data[i, 1]
        # 根据Taylor值调整缩放因子 (adjust scaling factor as needed)
        # ss = int(5000 * (abs(a) + abs(b)) / 2)
        ss = int(5000 * (abs(b)) / 2)
        ax.scatter(x, y, color='r', s=ss)

    # 绘制骨骼连接线 (plot bone connections)
    for connections in sk_config:
        for i in range(len(connections) - 1):
            start_joint = connections[i]
            end_joint = connections[i + 1]
            ax.plot([frame_data[start_joint, 0], frame_data[end_joint, 0]],
                    [frame_data[start_joint, 1], frame_data[end_joint, 1]], color='b')

            # 设置相等的比例 (set equal aspect ratio)
    ax.set_aspect('equal')


# 创建图像和坐标轴 (create figure and axis)
fig, ax = plt.subplots(figsize=(8, 8))

# 初始化显示第一帧 (initialize with the first frame)
plot_skeleton_frame_2d(skeleton[:, :, 0], taylorskeleton[:, :, 0], sk_config, ax)


# 定义动画更新函数 (update function for animation)
def update(frame):
    plot_skeleton_frame_2d(skeleton[:, :, frame], taylorskeleton[:, :, frame], sk_config, ax)


# 创建动画，这里使用Taylor变换后帧数 (create animation using Taylor-transformed frames)
ani = FuncAnimation(fig, update, frames=num_taylor, interval=100)  # Interval in milliseconds

html_anim = HTML(ani.to_jshtml())
display(html_anim)

# 关闭图像以避免重复显示 (close the plot)
plt.close()


## 4. 对骨架序列计算Taylor视频 (Compute Taylor videos on skeleton sequences)

In [26]:
# 以下代码用于遍历文件夹中的所有.mat文件，并对每个文件进行Taylor变换
# 注意：在实际运行前，请确保目录路径和文件名符合要求 (make sure the directory path and filenames are correct)

# import os

# # 指定目录路径 (directory path)
# directory = 'skeleton'

# # 遍历目录中的所有文件 (loop through files in the directory)
# for filename in os.listdir(directory):
#     # 检查文件是否以'.mat'结尾 (check if file ends with '.mat')
#     if filename.endswith('.mat'):
#         # 构建文件的完整路径 (full path of the file)
#         filepath = os.path.join(directory, filename)
#         # 处理该文件 (process the file as needed)
#         taylorskeleton = taylor_video(filepath, 1, 4)
#         # 生成新的文件名，在'.mat'前添加'taylor' (new filename with 'taylor' added before '.mat')
#         new_filename = filename.replace('.mat', 'taylor.mat')
#         new_filepath = os.path.join(directory, new_filename)
#         # 打印处理文件信息 (print processing information)
#         print(f'处理文件: {filepath}')
#         taylorskeleton_array = taylorskeleton.double().numpy()

#         # 保存numpy数组到mat文件中，键为'skeletonsequence'
#         io.savemat(new_filepath, {'skeletonsequence': taylorskeleton_array}, appendmat=False, format='5')
